In [1]:
%pip install python-dotenv datasets mistralai faiss-cpu


[notice] A new release of pip is available: 24.3.1 -> 25.1.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [2]:
from dotenv import load_dotenv
import os
load_dotenv() 

True

In [7]:
%pip install --upgrade pip


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 936.1 kB/s eta 0:00:00a 0:00:01
  Attempting uninstall: pip
    Found existing installation: pip 24.3.1
    Uninstalling pip-24.3.1:
      Successfully uninstalled pip-24.3.1
Note: you may need to restart the kernel to use updated packages.


In [5]:
import numpy as np
import faiss
from datasets import load_dataset
from mistralai.client import MistralClient

ValueError: numpy.dtype size changed, may indicate binary incompatibility. Expected 96 from C header, got 88 from PyObject

In [5]:
client = MistralClient(api_key="SUGMaHZZsTJeiDYd77JBDsYRG48iOPtj") 
model_name = "open-mistral-7b"

In [6]:
# Define a function to generate embeddings using Mistral's embedding endpoint
def get_text_embedding(text):
    # Send a request to the Mistral embedding endpoint with the given text
    response = client.embeddings(model="mistral-embed", input=[text])
    # Convert the returned embedding to a numpy float32 array
    embedding = np.array(response.data[0].embedding).astype("float32")
    return embedding

In [7]:
# --- Load and Prepare the HotpotQA Dataset ---
# For demonstration, we load the first 1000 examples from the "distractor" split of HotpotQA
dataset = load_dataset("hotpot_qa", "distractor", split="train[:1000]")

2025-04-30 15:20:10,260 WARNING datasets.builder: Found cached dataset hotpot_qa (/Users/akhilelamanchili/.cache/huggingface/datasets/hotpot_qa/distractor/1.0.0/133b9501f892e5193babbad937bee3b4899deb4691ef4d791e6ac0111c875bb5)


In [8]:
# Create a list of documents by concatenating the context paragraphs for each example
documents = []
for example in dataset:
    context_dict = example["context"]
    # Join all the titles (if any)
    titles = " ".join(context_dict.get("title", []))
    # For sentences, context_dict["sentences"] is a list of lists, so flatten them:
    sentences = " ".join([" ".join(sent_list) for sent_list in context_dict.get("sentences", [])])
    # Combine titles and sentences to form the document
    document_text = titles + " " + sentences
    documents.append(document_text)

print("Loaded", len(documents), "documents.")



Loaded 1000 documents.


In [10]:
from tqdm import tqdm
import numpy as np

# --- Generate Embeddings and Build FAISS Index ---

# Initialize an empty list to store embeddings
embeddings_list = []

print("Starting to generate embeddings for each document...")
for i, doc in enumerate(tqdm(documents, desc="Embedding Documents", unit="doc")):
    # Get embedding for the current document
    embedding = get_text_embedding(doc)
    embeddings_list.append(embedding)
    # Optionally print progress every 50 documents (adjust as needed)
    if (i + 1) % 50 == 0:
        print(f"Processed {i + 1}/{len(documents)} documents.")

# Stack all embeddings into a numpy array
embeddings = np.stack(embeddings_list)
d = embeddings.shape[1]  # Dimension of the embeddings

print("Finished generating embeddings.")
print("Total embeddings shape:", embeddings.shape)

Starting to generate embeddings for each document...


Embedding Documents:   5%|▌         | 50/1000 [01:26<18:22,  1.16s/doc]

Processed 50/1000 documents.


Embedding Documents:  10%|█         | 100/1000 [03:05<16:10,  1.08s/doc]

Processed 100/1000 documents.


...

Embedding Documents:  95%|█████████▌| 950/1000 [28:37<02:13,  2.68s/doc]

Processed 950/1000 documents.


Embedding Documents: 100%|██████████| 1000/1000 [30:11<00:00,  1.81s/doc]

Processed 1000/1000 documents.


Finished generating embeddings.
Total embeddings shape: (1000, 1024)


In [11]:
# Build a FAISS index using L2 (Euclidean) distance
index = faiss.IndexFlatL2(d)
index.add(embeddings)
print("FAISS index built with", index.ntotal, "vectors.")

FAISS index built with 1000 vectors.


In [12]:
print(documents)

['Radio City (Indian radio station) History of Albanian football Echosmith Women\'s colleges in the Southern United States First Arthur County Courthouse and Jail Arthur\'s Magazine 2014–15 Ukrainian Hockey Championship First for Women Freeway Complex Fire William Rast Radio City is India\'s first private FM radio station and was started on 3 July 2001.  It broadcasts on 91.1 (earlier 91.0 in most cities) megahertz from Mumbai (where it was started in 2004), Bengaluru (started first in 2001), Lucknow and New Delhi (since 2003).  It plays Hindi, English and regional songs.  It was launched in Hyderabad in March 2006, in Chennai on 7 July 2006 and in Visakhapatnam October 2007.  Radio City recently forayed into New Media in May 2008 with the launch of a music portal - PlanetRadiocity.com that offers music related news, videos, songs, and other music-related features.  The Radio station currently plays a mix of Hindi and Regional music.  Abraham Thomas is the CEO of the company. Football 

In [13]:
# --- Define the Retrieval Function ---
def retrieve_documents(query, documents, index, k=3):
    """
    Embed the query, search for the top-k most similar documents, 
    and return the concatenated text of these documents.
    """
    q_embedding = get_text_embedding(query)
    q_embedding = np.array([q_embedding])
    distances, indices = index.search(q_embedding, k)
    retrieved_text = " ".join([documents[i] for i in indices[0]])
    return retrieved_text


In [14]:
from pydantic import BaseModel

class ChatMessage(BaseModel):
    role: str
    content: str

In [15]:
# --- Define the Mistral Chat Call ---
def run_mistral(prompt):
    """
    Sends the prompt to the Mistral Chat API and returns the generated response.
    Uses the updated message format (list of dictionaries).
    """
    messages = [ChatMessage(role="user", content=prompt)]
    response = client.chat(model=model_name, messages=messages)
    return response.choices[0].message.content

In [16]:
# --- Standard RAG Pipeline ---
def standard_rag(query, documents, index):
    """
    Retrieve context based on the query and then generate an answer using the Mistral Chat API.
    """
    retrieved_context = retrieve_documents(query, documents, index, k=5)
    print("Retrieved Context:", retrieved_context)
    prompt = (
        f"Answer the following question based on the provided context.\n\n"
        f"Context: {retrieved_context}\n\n"
        f"Question: {query}\n"
        f"Answer:"
    )
    return run_mistral(prompt)

In [22]:
def multi_hop_rag(query, documents, index):
    """
    Retrieve multiple contexts based on the query using multi-hop retrieval, 
    then generate an answer by synthesizing the information from those contexts.
    """
    
    # Step 1: First-hop retrieval - Retrieve initial context based on the query
    first_retrieved_context = retrieve_documents(query, documents, index, k=5)
    print("First-hop Retrieved Context:", first_retrieved_context)
    
    # Step 2: Use the first-hop context to refine the query and retrieve the second hop
    refined_query = refine_query(query, first_retrieved_context)
    second_retrieved_context = retrieve_documents(refined_query, documents, index, k=5)
    print("Second-hop Retrieved Context:", second_retrieved_context)
    
    # Combine both first-hop and second-hop context
    combined_context = first_retrieved_context + "\n" + second_retrieved_context

    # Step 3: Generate the final answer using the combined context
    prompt = (
        f"Answer the following question based on the provided context.\n\n"
        f"Context: {combined_context}\n\n"
        f"Question: {query}\n"
        f"Answer:"
    )
    
    return run_mistral(prompt)

def refine_query(query, context):
    """
    Refine the original query based on the information retrieved from the first-hop context.
    This could involve rephrasing or specifying further details to guide the next hop retrieval.
    """
    # Example: You might extract additional information from the context to create a more detailed query
    # For simplicity, here we just append the first-hop context to the query.
    refined_query = query + " " + context[:500]  # Taking the first 500 characters of context as refinement
    return refined_query


In [21]:
query = "Which country has the largest population, and what is its official language?"
answer = standard_rag(query, documents, index)
print("Query:", query)
print("Answer:", answer)

Retrieved Context: Demography of the United Kingdom Orleans, Ontario Kerry Saxby-Junna Blennerville Islam in West Bengal Korçë Young, New South Wales Northern Region, Manitoba Warton, Lancaster Ackworth, West Yorkshire According to the 2011 census, the total population of the United Kingdom was around 63,182,000. <ref name="2http://www.ons.gov.uk/ons/dcp171778_292378.pdf |title=2011 Census: Population Estimates for the United Kingdom |publisher=Office for National Statistics |date=27 March 2011 |accessdate=18 December 2012 }}</ref> It is the 22nd-largest in the world.  Its overall population density is 259 people per square kilometre (671 people per sq mi), with England having a significantly higher population density than Wales, Scotland and Northern Ireland.  Almost one-third of the population lives in England's southeast, which is predominantly urban and suburban, with about 8 million in the capital city of London, the population density of which is just over 5,200 per square kilome

In [25]:
query = "What is the relationship between Apollo 11 and the first moon landing?"
answer = multi_hop_rag(query, documents, index)
print("Answer:", answer)

First-hop Retrieved Context: Buzz Aldrin Lunar plaque Apollo 13 (film) Canceled Apollo missions Apollo 21 Moon Landing (music drama) Alan Bean Soviet crewed lunar programs First on the Moon (1970 book) Apollo 10 Buzz Aldrin (born Edwin Eugene Aldrin Jr.; January 20, 1930) is an American engineer and former astronaut.  As the Lunar Module Pilot on Apollo 11, he was one of the first two humans to land on the Moon, and the second person to walk on it.  He set foot on the Moon at 03:15:16 on July 21, 1969 (UTC), following mission commander Neil Armstrong.  He is a former U.S. Air Force officer with the Command Pilot rating.  He also went into orbit on the Gemini 12 mission, finally achieving the goals for EVA (space-walk work) that paved the way to the Moon and success for the Gemini program; he spent over five hours on EVA on that mission. Stainless steel commemorative plaques measuring 9 by were attached to the ladders on the descent stages of the United States Apollo Lunar Modules flown